In [14]:
import pandas as pd
import jinja2
import json
from IPython.display import display, display_pretty, Javascript, HTML

In [15]:
pd_input_matrix = pd.read_csv("data/wgEncodeBroadHistoneHmecH3k4me3StdSig.txt",delim_whitespace=True)
test_matrix = pd_input_matrix.to_json(orient="split")

In [16]:
test_metaplot = pd_input_matrix.mean(axis=0).to_json(orient="split")

In [17]:
with open("data/no_sort.json") as f:
    analysis_data = json.load(f)

In [19]:
test_template = jinja2.Template( 
"""
<head>
    <script src="//d3js.org/d3.v3.min.js" charset="utf-8"></script>
</head>
<style>
body {
  font: 10px sans-serif;
}
#display{
    width: 90%;
    height: 800px;
    left: 5%;
    position: relative;
    overflow: visible;
}
#left_panel{
    width: 40%;
    height: 100%;
    left: 0;
    top: 0;
    postion: absolute;
    overflow: visible;
}
#right_panel{
    width: 60%;
    height: 100%;
    left: 40%;
    top: 0;
    position: absolute;
}
#heatmap{
    width: 100%;
    height: 90%;
    left: 0%;
    top: 10%;
    position: absolute;
    //overflow-y: scroll;
}
#sort_button{
    //top: 50px;
    //left: 10%;
    //width: 200px;
    //position: absolute;
}
#heatmap_header{
    width: 100%;
    height: 10%;
    top: 0;
    left: 0%;
    position: absolute;
    overflow: visible;
}
#metaplot{
    height: 30%;
    //background-color: cyan;
    overflow: visible;
}
path {
    stroke: steelblue;
    stroke-width: 1;
    fill: none;
}
.axis {
    shape-rendering: crispEdges;
}
.x.axis line {
    stroke: #000;
}
.x.axis .minor {
    //stroke-opacity: .5;
    stroke: #000;
}
.x.axis path {
    stroke: #000;
}
.y.axis line, .y.axis path {
    fill: none;
    stroke: #000;
}
</style>
<body>
<div id="display">
    <div id="left_panel">
        <h1>Select sort order</h1>
        <select id="sort_button">
            <option value="Feature list order">Feature list order</option>
        </select>
        <h1>Metaplot</h1>
        <div class="plot" id="metaplot"/>
    </div>
    <div id="right_panel">
        <div class="heatmap" id="heatmap"/>
        <div class="heatmap_header" id="heatmap_header"/>
    </div>
</div>
</body>
<script>

function writeMetaPlot() {

    var div_height = document.getElementById("metaplot").clientHeight,
        div_width = document.getElementById("metaplot").clientWidth;

    var m = {"top":0.1*div_height, "bottom":0.15*div_height, "left":0.15*div_width, "right":0.05*div_width}
    h = div_height - m.top - m.bottom
    w = div_width - m.left - m.right;
    
    var scatter_points = [];
    
    for (var i = 0; i < metaplot_data["data"].length; i++) {
        scatter_points.push([(parseInt(metaplot_data["index"][i].split(":")[0])+parseInt(metaplot_data["index"][i].split(":")[1]))/2, metaplot_data["data"][i]]);
    }
    
    var y = d3.scale.linear().domain([0, d3.max(metaplot_data["data"])]).range([h, 0]);
    var x = d3.scale.linear().domain([metaplot_data["index"][0].split(":")[0], metaplot_data["index"][metaplot_data["index"].length-1].split(":")[1]]).range([0, w]);

    var line = d3.svg.line()
        .x(function(d) { return x(d[0]);})
        .y(function(d) { return y(d[1]);});
    
    var graph = d3.select("#metaplot").append("svg:svg")
        .attr("width", div_width)
        .attr("height", div_height)
        .append("svg:g")
        .attr("transform", "translate(" + m.left + "," + m.top + ")");
        
    var xAxis = d3.svg.axis().scale(x).ticks(4).tickSubdivide(true);
    graph.append("svg:g")
        .attr("class", "x axis")
        .attr("transform", "translate(0," + h + ")")
        .call(xAxis);
        
    var yAxisLeft = d3.svg.axis().scale(y).ticks(4).orient("left");
    graph.append("svg:g")
        .attr("class", "y axis")
        //.attr("transform", "translate(" + m.left + ",0)")
        .call(yAxisLeft);
    
    graph.append("svg:path").attr("d", line(scatter_points));
}

function writeHeatmapHeader() {
    var div_height = document.getElementById("heatmap_header").clientHeight,
        div_width = document.getElementById("heatmap_header").clientWidth;

    var range_start = heatmap_data["columns"][0].split(":")[0],
        range_end = heatmap_data["columns"][heatmap_data["columns"].length-1].split(":")[1];

    //console.log(range_start);
    //console.log(range_end);

    var zero_position = div_width/(range_end-range_start)*(0-range_start);

    //console.log(div_width);
    //console.log(zero_position);

    var svg = d3.select("#heatmap_header")
        .append("svg")
        .attr("width", div_width)
        .attr("height", div_height)
        .style("overflow", "visible");

    var header_lines = [
        {text: range_start, position: 0},
        {text: range_end, position: div_width},
        {text: "0", position: zero_position}
    ];

    svg.append("g")
        .selectAll("line")                 
        .data(header_lines)
        .enter()
        .append("line")
        .attr("x1", function(d) {return d.position;})
        .attr("x2", function(d) {return d.position;})
        .attr("y1", 0.6*div_height)
        .attr("y2", 0.9*div_height)
        .style("stroke", "black")
        .style("stroke-width", 1);

    svg.append("line")
        .attr("x1", 0)
        .attr("x2", div_width)
        .attr("y1", 0.9*div_height)
        .attr("y2", 0.9*div_height)
        .style("stroke", "black")
        .style("stroke-width", 1);

    svg.append("g")
        .selectAll("text")                 
        .data(header_lines)
        .enter()
        .append("text")
        .text(function(d) { return d.text;})
        .attr("x", function(d) {return d.position;})
        .attr("y", 0.45*div_height)
        .attr("font-family", "sans-serif")
        .attr("font-size", "12px")
        .attr("fill", "black")
        .style("text-anchor", "middle");
}

function writeData(value) {
    var index = sort_data.map(function(x) {return x.data_set; }).indexOf(value);
    for (var i = 0; i < sort_data[index]["sort_order"].length; i++) {
        for (var j = 0; j < heatmap_data["data"][i].length; j++) {
            context.beginPath();
            context.rect(j, i, 1, 1);
            context.fillStyle=colorScale(heatmap_data["data"][sort_data[index]["sort_order"][i]][j]);
            context.fill();
            context.closePath();
        }
    }
}

var heatmap_data = {{heatmap_data}};
var analysis_data = {{analysis_data}};
var metaplot_data = {{metaplot_data}};

var row_number = heatmap_data["index"].length;
var col_number = heatmap_data["columns"].length;

var sort_data = analysis_data["sort_orders"];

sort_data.unshift({"data_set":"Feature list order", "sort_order":Array.apply(null, {length: row_number}).map(Number.call, Number)});

document.getElementById("sort_button").setAttribute("onchange", "writeData(this.value)");

//console.log(sort_data);

var sort_button = d3.select("#sort_button")
    .selectAll("option")
    .data(sort_data)
    .enter()
    .append("option")
    .text(function(d) {return d.data_set;})
    .attr("value", function(d) {return d.data_set;});

//console.log(row_number);
//console.log(col_number);

var base = d3.select("#heatmap");
var chart = base.append("canvas")
  .attr("width", document.getElementById("heatmap").clientWidth)
  .attr("height", document.getElementById("heatmap").clientHeight);

var context = chart.node().getContext("2d");

var data_max = -Infinity;

for (var i = 0; i < heatmap_data["data"].length; i++) {
    for (var j = 0; j < heatmap_data["data"][i].length; j++) {
        if (heatmap_data["data"][i][j] > data_max) data_max = heatmap_data["data"][i][j];
    }
}

//console.log(data_max);

var colorScale = d3.scale.linear()
    .domain([0, 0.2*data_max])
    .range(['white','red']);

//console.log(heatmap_data["data"].length);
//console.log(heatmap_data["data"][0].length);

var scale_x = document.getElementById("heatmap").clientWidth/col_number;
var scale_y = document.getElementById("heatmap").clientHeight/row_number;

//console.log(scale_x);
//console.log(scale_y);

context.scale(scale_x,scale_y);

writeData("Feature list order");
writeHeatmapHeader();
writeMetaPlot();
/*
for (var i = 0; i < heatmap_data["data"].length; i++) {
    for (var j = 0; j < heatmap_data["data"][i].length; j++) {
        context.beginPath();
        context.rect(j, i, 1, 1);
        context.fillStyle=colorScale(heatmap_data["data"][i][j]);
        context.fill();
        context.closePath();
    }
}
*/
</script>
"""
)
display(HTML(test_template.render(heatmap_data=test_matrix, analysis_data=analysis_data, metaplot_data=test_metaplot)))